# Capstone Project - The Battle of the Neighborhoods
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening an **Indian restaurant** in **Pune**, India.

Since there are lots of restaurants in Pune we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no Indian restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to Indian restaurants in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Google Maps API reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Pune center will be obtained using **Google Maps API geocoding** of well known Pune location (Deccan)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 10x10 killometers centered around Pune city center.

Let's first find the latitude & longitude of Pune city center, using specific, well known address and Google Maps geocoding API.

In [8]:
# The code was removed by Watson Studio for sharing.

In [9]:
import requests

def get_coordinates(api_key, address, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]
    
address = 'Deccan, Pune, India'
pune_center = get_coordinates(google_api_key, address)
print('Coordinate of {}: {}'.format(address, pune_center))

Coordinate of Deccan, Pune, India: [18.5165436, 73.8366021]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~10km from Deccan. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [10]:
!pip install shapely
import shapely.geometry

!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Pune center longitude={}, latitude={}'.format(pune_center[1], pune_center[0]))
x, y = lonlat_to_xy(pune_center[1], pune_center[0])
print('Pune center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Pune center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Pune center longitude=73.8366021, latitude=18.5165436
Pune center UTM X=7719971.255662321, Y=3660371.9443684192
Pune center longitude=73.8366020999998, latitude=18.516543599995305


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [11]:
pune_center_x, pune_center_y = lonlat_to_xy(pune_center[1], pune_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = pune_center_x - 10000
x_step = 1050
y_min = pune_center_y - 10000 - (int(21/k)*k*1050 - 20000)/2
y_step = 1050 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):    
#for i in range(0, 42):    
    y = y_min + (i * y_step)
    
    x_offset = 600 if i%2==0 else 0
    for j in range(0, 21):
        #x = x_min + (i * x_step)
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(pune_center_x, pune_center_y, x, y)
        if (distance_from_center <= 10001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

321 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [13]:
!pip install folium

import folium

     |████████████████████████████████| 92kB 18.7MB/s eta 0:00:01


In [15]:
map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.Marker(pune_center, popup='Pune').add_to(map_pune)
for lat, lon in zip(latitudes, longitudes):
    #folium.Circle([lat, lon], radius=250, color='blue').add_to(map_pune) 
    folium.Circle([lat,lon], radius=300, color='blue', fill=False).add_to(map_pune)
    #folium.Marker([lat, lon]).add_to(map_pune)
map_pune

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~10km from Deccan. 

Let's now use Google Maps API to get approximate addresses of those locations.

In [16]:

def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        return address
    except:
        return None

addr = get_address(google_api_key, pune_center[0], pune_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(pune_center[0], pune_center[1], addr))

Reverse geocoding check
-----------------------
Address of [18.5165436, 73.8366021] is: 619, behind sai petrol pump, Deccan Gymkhana, Pune, Maharashtra 411004, India


In [17]:
# Try to load from local file system in case we did this before
import pandas as pd
import pickle

df_locations = []
loaded = False
try:
    with open('locations_3500.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

if not loaded:
    print('Obtaining location addresses: ', end='')
    addresses = []
    for lat, lon in zip(latitudes, longitudes):
        address = get_address(google_api_key, lat, lon)
        if address is None:
            address = 'NO ADDRESS'
        address = address.replace(', India', '') # We don't need country part of address
        addresses.append(address)
        print(' .', end='')
    print(' done.')

    df_locations = pd.DataFrame({'Address': addresses,
                                 'Latitude': latitudes,
                                 'Longitude': longitudes,
                                 'X': xs,
                                 'Y': ys,
                                 'Distance from center': distances_from_center})
    df_locations.to_pickle('./locations3500.pkl')    
    df_locations.head(10)
    
    # Let's persists this in local file system
    with open('locations3500.pkl', 'wb') as f:
        pickle.dump(df_locations, f)


Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [18]:
addresses[50:70]

['47/43, Chaitanya Nagar, Kothrud, Pune, Maharashtra 411058',
 '#4 , VIHAR APARTMENTS, Dahanukar Colony, Kothrud, Pune, Maharashtra 411038',
 'Gaikwad chowl near boudh vihar karvenagar pune52 Gaikwad chowl near boudh vihar karvenagar pune52, Kamana Vasahat, Hingne Budrukh, Karve Nagar, Pune, Maharashtra 411052',
 'Vitthal Mandir Karvenagar, Karve Nagar, Pune, Maharashtra 411052',
 'Ruturang, Rajaram Bridge, opp. Vithal Mandir, Jaydeo Nagar, Dattawadi, Pune, Maharashtra 411052',
 'Anand Vihar, Anand Vihar Tekdi Rasta, Mahadev Nagar, Vadgaon Budruk, Pune, Maharashtra 411009',
 'Unnamed Road, Taljai Forest Area, Pune, Maharashtra 411009',
 'D-502, Rajyavahatuk society, Parvati Paytha, Pune, Maharashtra 411009',
 '65, Kiran Housing Society, Parvati Paytha, Pune, Maharashtra 411009',
 '65/2, Padmavati Sahakar Nagar Rd, Adhyapak Colony, Sahakar Nagar, Parvati Paytha, Pune, Maharashtra 411009',
 '42, Gururaj Society - 3, Shree Sant Eknath Nagar, Bibwewadi, Pune, Maharashtra 411037',
 'Unnamed

Looking good. Let's now place all this into a Pandas dataframe.

In [19]:
df_locations.head(10)

Address   Latitude  Longitude  \
0  Madhukar Apartment plat No.46, AtulNagar Phase...  18.484477  73.792840   
1  135/1A, Navbharat Society, गिरीधर नगर, वारजे, ...  18.481888  73.797963   
2  S.No. 140/8/1, NDA Road Near Warje Main Square...  18.479300  73.803085   
3          10, NH 4, Warje, Pune, Maharashtra 411052  18.476712  73.808206   
4  C5-102, Sun Empire, Anand Nagar, sinhagad road...  18.474124  73.813327   
5          33, Anand Nagar, Pune, Maharashtra 411051  18.471536  73.818446   
6  Shop no. 1, Jay Malhar Bldg. Jadhav Nagar Road...  18.468948  73.823565   
7  Shop no 2, sunanda Apartment, Gosavi Vasti, Va...  18.466361  73.828683   
8  Sai Sayaji Nagar, Renuka Nagar, Urit Nagar, Wa...  18.490190  73.792262   
9  Ankur warje, Motiram Nagar, Warje, Pune, Mahar...  18.487601  73.797385   

              X             Y  Distance from center  
0  7.715821e+06  3.651279e+06           9995.498987  
1  7.716871e+06  3.651279e+06           9607.158789  
2  7.717921e+06  3.651279e+06           9321.480569  
3  7.718971e+06  3.651279e+06           9148.087232  
4  7.720021e+06  3.651279e+06           9093.404203  
5  7.721071e+06  3.651279e+06           9159.557850  
6  7.722121e+06  3.651279e+06           9343.982021  
7  7.723171e+06  3.651279e+06           9639.891078  
8  7.715221e+06  3.652188e+06           9462.524769  
9  7.716271e+06  3.652188e+06           8981.473988

...and let's now save/persist this data into local file.

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Indian restaurant' category, as we need info on Indian restaurants in the neighborhood.

Foursquare credentials are defined in hidden cell bellow.

In [20]:
# The code was removed by Watson Studio for sharing.

In [21]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

indian_restaurant_categories =['4bf58dd8d48988d10f941735','54135bf5e4b08f3d2429dfe5', '54135bf5e4b08f3d2429dff3',
                                '54135bf5e4b08f3d2429dff5','54135bf5e4b08f3d2429dfe2','54135bf5e4b08f3d2429dff2',
                                '54135bf5e4b08f3d2429dfe1','54135bf5e4b08f3d2429dfe3','54135bf5e4b08f3d2429dfe8',
                                '54135bf5e4b08f3d2429dfe9','54135bf5e4b08f3d2429dfe6','54135bf5e4b08f3d2429dfdf',
                                '54135bf5e4b08f3d2429dfe4','54135bf5e4b08f3d2429dfe7','54135bf5e4b08f3d2429dfea',
                                '54135bf5e4b08f3d2429dfeb','54135bf5e4b08f3d2429dfed','54135bf5e4b08f3d2429dfee',
                                '54135bf5e4b08f3d2429dff4','54135bf5e4b08f3d2429dfe0','54135bf5e4b08f3d2429dfdd',
                                '54135bf5e4b08f3d2429dff6','54135bf5e4b08f3d2429dfef','54135bf5e4b08f3d2429dff0',
                                '54135bf5e4b08f3d2429dff1','54135bf5e4b08f3d2429dfde','54135bf5e4b08f3d2429dfec']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Maharashtra', '')
    address = address.replace(', India', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [22]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
#    italian_restaurants = {}
    indian_restaurants = {}
    chinese_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, foursquare_client_id, foursquare_client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
#           is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
            is_res, is_indian= is_restaurant(venue_categories, specific_filter=indian_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
#                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_italian, x, y)
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_indian, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
#                if is_italian:
#                    italian_restaurants[venue_id] = restaurant
                if is_indian:
                    indian_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
#    return restaurants, italian_restaurants, location_restaurants
    return restaurants, indian_restaurants, location_restaurants


# Try to load from local file system in case we did this before
restaurants = {}
indian_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_3500.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('italian_restaurants_3500.pkl', 'rb') as f:
        italian_restaurants = pickle.load(f)
    with open('indian_restaurants_3500.pkl', 'rb') as f:
        indian_restaurants = pickle.load(f)
    with open('location_restaurants_3500.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
#    restaurants, italian_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    restaurants, indian_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    # Let's persists this in local file system
    with open('restaurants_3500.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
#    with open('italian_restaurants_3500.pkl', 'wb') as f:
#        pickle.dump(italian_restaurants, f)
    with open('indian_restaurants_3500.pkl', 'wb') as f:
        pickle.dump(indian_restaurants, f)    
    with open('location_restaurants_3500.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
        

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [23]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
#print('Total number of Italian restaurants:', len(italian_restaurants))
print('Total number of Indian restaurants:', len(indian_restaurants))
#print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(restaurants) * 100))
print('Percentage of Indian restaurants: {:.2f}%'.format(len(indian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 514
Total number of Indian restaurants: 310
Percentage of Indian restaurants: 60.31%
Average number of restaurants in neighborhood: 1.3738317757009346


In [24]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4da0387de804530cb5b28576', 'Preet Da Dhaba', 18.486955695994904, 73.79187226295471, 'Warje, Pune 411038, Mahārāshtra', 294, True, 7715446.214137539, 3651612.4263406084)
('550ed821498e069e34d5ce22', 'Highway 47', 18.484092861381086, 73.79801973864609, 'India', 245, True, 7716684.50364708, 3651653.3145109853)
('53d26f77498e73f439f8939d', 'Amrapali Family Restaurant', 18.48396687072949, 73.80003607565818, 'Opp Mai Mangeshkat Hospital, Warje (Off Mumbai-pune Bypass), Pune, Mahārāshtra', 318, True, 7717018.45673797, 3651803.1333916592)
('50add345e4b00a661b559eda', 'sai krupa hotel', 18.483198600140952, 73.80089775190847, 'Mumbai Banglore Highway,warje,pune', 342, False, 7717224.661821749, 3651747.3058106606)
('57b0a2f5498ed9369df0c9a0', 'Hotel Swarna Pure Veg', 18.480503, 73.8034, 'Near Warje Fly Over (Adjecent To Lodha Hospital), Pune 411058, Mah', 137, False, 7717864.78934928, 3651507.2264639433)
('511f636ce4b0f5542f9c20d8', 'Kanshika', 18

In [25]:
#print('List of Italian restaurants')
print('List of Indian restaurants')
print('---------------------------')
#for r in list(italian_restaurants.values())[:10]:
#    print(r)
for r in list(indian_restaurants.values())[:10]:
    print(r)    
print('...')
#print('Total:', len(italian_restaurants))
print('Total:', len(indian_restaurants))

List of Indian restaurants
---------------------------
('4da0387de804530cb5b28576', 'Preet Da Dhaba', 18.486955695994904, 73.79187226295471, 'Warje, Pune 411038, Mahārāshtra', 294, True, 7715446.214137539, 3651612.4263406084)
('550ed821498e069e34d5ce22', 'Highway 47', 18.484092861381086, 73.79801973864609, 'India', 245, True, 7716684.50364708, 3651653.3145109853)
('53d26f77498e73f439f8939d', 'Amrapali Family Restaurant', 18.48396687072949, 73.80003607565818, 'Opp Mai Mangeshkat Hospital, Warje (Off Mumbai-pune Bypass), Pune, Mahārāshtra', 318, True, 7717018.45673797, 3651803.1333916592)
('511f636ce4b0f5542f9c20d8', 'Kanshika', 18.476186752319336, 73.8075180053711, 'Karvenagar, Pune, Mahārāshtra', 93, True, 7718907.719401701, 3651132.195109534)
('4e3bce7045dd68e327222eff', 'Indian Flavours', 18.475872488301242, 73.8126334104767, 'India', 207, True, 7719754.776757509, 3651513.3354711095)
('5a5b13d0e4c4594bf189c1f3', 'The Green Roof', 18.472858, 73.821266, 'Manikbaug, Sinhagd Road (opposi

In [26]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: Rolling Shawarma
Restaurants around location 102: IDDOS, Chaitanya Paranthas, Hot Sip, Harsh, Chaitanya Garden, Palavi Veg Restaurant
Restaurants around location 103: Tiranga, YUM DUM express
Restaurants around location 104: Offbeat, Olivia, Raj Restaurant
Restaurants around location 105: Abhishek Veg, Purepur Kolhapur, Multi Spice, Abhishek Non Veg
Restaurants around location 106: Harvest Club
Restaurants around location 107: Lavangi Mirchi Kolhapurchi
Restaurants around location 108: 
Restaurants around location 109: 
Restaurants around location 110: Jagat Bhari Kolhapuri Restaurant, Mankar Dosa Centre, Kolhapuri Katta, Vedant Veg, Tiranga, Hotel Baasuri


Let's now see all the collected restaurants in our area of interest on map, and let's also show Italian restaurants in different color.

In [27]:
map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.Marker(pune_center, popup='Deccan').add_to(map_pune)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    is_chinese = res[6]
    is_indian = res[6]
    color = 'red' if is_italian else 'blue'
    color = 'red' if is_chinese else 'blue'
    color = 'red' if is_indian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_pune)
map_pune

Looking good. So now we have all the restaurants in area within few kilometers from Deccan, and we know which ones are Indian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Pune that have low restaurant density, particularly those with low number of Indian restaurants. We will limit our analysis to area ~10km around city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 10km from Pune center** (Deccan). We have also **identified Indian restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of Pune - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Indian restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without Indian restaurants in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [28]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 1.3738317757009346


Address   Latitude  Longitude  \
0  Madhukar Apartment plat No.46, AtulNagar Phase...  18.484477  73.792840   
1  135/1A, Navbharat Society, गिरीधर नगर, वारजे, ...  18.481888  73.797963   
2  S.No. 140/8/1, NDA Road Near Warje Main Square...  18.479300  73.803085   
3          10, NH 4, Warje, Pune, Maharashtra 411052  18.476712  73.808206   
4  C5-102, Sun Empire, Anand Nagar, sinhagad road...  18.474124  73.813327   
5          33, Anand Nagar, Pune, Maharashtra 411051  18.471536  73.818446   
6  Shop no. 1, Jay Malhar Bldg. Jadhav Nagar Road...  18.468948  73.823565   
7  Shop no 2, sunanda Apartment, Gosavi Vasti, Va...  18.466361  73.828683   
8  Sai Sayaji Nagar, Renuka Nagar, Urit Nagar, Wa...  18.490190  73.792262   
9  Ankur warje, Motiram Nagar, Warje, Pune, Mahar...  18.487601  73.797385   

              X             Y  Distance from center  Restaurants in area  
0  7.715821e+06  3.651279e+06           9995.498987                    1  
1  7.716871e+06  3.651279e+06           9607.158789                    1  
2  7.717921e+06  3.651279e+06           9321.480569                    1  
3  7.718971e+06  3.651279e+06           9148.087232                    1  
4  7.720021e+06  3.651279e+06           9093.404203                    1  
5  7.721071e+06  3.651279e+06           9159.557850                    0  
6  7.722121e+06  3.651279e+06           9343.982021                    1  
7  7.723171e+06  3.651279e+06           9639.891078                    0  
8  7.715221e+06  3.652188e+06           9462.524769                    0  
9  7.716271e+06  3.652188e+06           8981.473988                    1

OK, now let's calculate the **distance to nearest Indian restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [29]:
distances_to_indian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in indian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_indian_restaurant.append(min_distance)

df_locations['Distance to Indian restaurant'] = distances_to_indian_restaurant

In [30]:
df_locations.head(10)

Address   Latitude  Longitude  \
0  Madhukar Apartment plat No.46, AtulNagar Phase...  18.484477  73.792840   
1  135/1A, Navbharat Society, गिरीधर नगर, वारजे, ...  18.481888  73.797963   
2  S.No. 140/8/1, NDA Road Near Warje Main Square...  18.479300  73.803085   
3          10, NH 4, Warje, Pune, Maharashtra 411052  18.476712  73.808206   
4  C5-102, Sun Empire, Anand Nagar, sinhagad road...  18.474124  73.813327   
5          33, Anand Nagar, Pune, Maharashtra 411051  18.471536  73.818446   
6  Shop no. 1, Jay Malhar Bldg. Jadhav Nagar Road...  18.468948  73.823565   
7  Shop no 2, sunanda Apartment, Gosavi Vasti, Va...  18.466361  73.828683   
8  Sai Sayaji Nagar, Renuka Nagar, Urit Nagar, Wa...  18.490190  73.792262   
9  Ankur warje, Motiram Nagar, Warje, Pune, Mahar...  18.487601  73.797385   

              X             Y  Distance from center  Restaurants in area  \
0  7.715821e+06  3.651279e+06           9995.498987                    1   
1  7.716871e+06  3.651279e+06           9607.158789                    1   
2  7.717921e+06  3.651279e+06           9321.480569                    1   
3  7.718971e+06  3.651279e+06           9148.087232                    1   
4  7.720021e+06  3.651279e+06           9093.404203                    1   
5  7.721071e+06  3.651279e+06           9159.557850                    0   
6  7.722121e+06  3.651279e+06           9343.982021                    1   
7  7.723171e+06  3.651279e+06           9639.891078                    0   
8  7.715221e+06  3.652188e+06           9462.524769                    0   
9  7.716271e+06  3.652188e+06           8981.473988                    1   

   Distance to Indian restaurant  
0                     502.040186  
1                     418.603761  
2                     997.280220  
3                     159.668359  
4                     355.070852  
5                     569.439192  
6                     774.842976  
7                     619.979176  
8                     616.952603  
9                     531.558826

In [31]:
print('Average distance to closest Indian restaurant from each area center:', df_locations['Distance to Indian restaurant'].mean())

Average distance to closest Indian restaurant from each area center: 811.8756008102923


OK, so **on average Indian restaurant can be found within ~500m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show **borders of Pune Wards** on our map and a few circles indicating distance of 1km, 2km and 3km from Deccan.

In [32]:
PuneAdminWards_URL = 'https://raw.githubusercontent.com/ipkunte/Coursera-Capstone-Project-/master/pune_admin_wards.geojson'
PuneAdminWards = requests.get(PuneAdminWards_URL).json()
print('GeoJson data loaded')

def wards_style(feature):
    return { 'color': 'blue', 'fill': False }

GeoJson data loaded


In [34]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

indian_latlons = [[res[2], res[3]] for res in indian_restaurants.values()]

In [35]:
from folium import plugins
from folium.plugins import HeatMap

map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_pune) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
folium.Circle(pune_center, radius=1000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=2000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=3000, fill=False, color='white').add_to(map_pune)
folium.GeoJson(PuneAdminWards, style_function=wards_style, name='geojson').add_to(map_pune)
map_pune

Looks like a few pockets of low restaurant density closest to city center can be found **North-West, south-west and west from Deccan**. 

Let's create another heatmap map showing **heatmap/density of Indian restaurants** only.

In [36]:
map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_pune) #cartodbpositron cartodbdark_matter
HeatMap(indian_latlons).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
folium.Circle(pune_center, radius=1000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=2000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=3000, fill=False, color='white').add_to(map_pune)
folium.GeoJson(PuneAdminWards, style_function=wards_style, name='geojson').add_to(map_pune)
map_pune

This map is not so 'hot' (Indian restaurants represent a subset of ~60% of all restaurants in Pune) but it also indicates higher density of existing Indian restaurants directly north-west and south-west from Deccan, with closest pockets of **low Indian restaurant density positioned west, south-west and north-west from city center**.

Based on this we will now focus our analysis on areas *south-west, north, south-west and east from Pune center* - we will move the center of our area of interest and reduce it's size to have a radius of **2.5km**. This places our location candidates mostly in boroughs **Kothrud and Karve Nagar** (another potentially interesting borough is **Pashan** with large low restaurant density north-west from city center, however this borough is less interesting to stakeholders).

### Kothrud and Karve Nagar

*"Kothrud is a former large town and currently one of the largest neighborhoods of Pune, one of the largest cities of Maharashtra state. It is one of the fastest developing suburb towns of Pune, with the population stably increasing for over 50 years. Kothrud is a center of education, with a few large colleges, as well as a center of shopping and commerce, with shopping areas like Big Bazaar, CityPride Kothrud, and others.

*"Karve Nagar is one of the largest urban districts located in Pune metropolitan area in Maharashtra, western India. It is bordered by Sadashiv Peth to the northeast, Vadgaon Budruk to the southeast, and Kothrud to the northwest. The area is divided into over 30 small sub-districts and is famous with a few large schools (including international ones), like TreeHouse School, and other.

Let's define new, more narrow region of interest, which will include low-restaurant-count parts of Kothrud and Karve Nagar closest to Deccan.

In [37]:
roi_x_min = pune_center_x - 5000
roi_y_max = pune_center_y - 500
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_pune = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_pune)
folium.GeoJson(PuneAdminWards, style_function=wards_style, name='geojson').add_to(map_pune)
map_pune

Not bad - this nicely covers all the pockets of low restaurant density in Kothrud and Karve Nagar closest to Pune center.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 250m appart).

In [38]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 250
y_step = 250 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

361 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Italian restaurant**.

In [39]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_indian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, indian_restaurants)
    roi_indian_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [40]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Indian restaurant':roi_indian_distances})

df_roi_locations.head(10)

Latitude  Longitude             X             Y  Restaurants nearby  \
0  18.497009  73.810422  7.717521e+06  3.654872e+06                   0   
1  18.500608  73.805860  7.716471e+06  3.655088e+06                   0   
2  18.499991  73.807080  7.716721e+06  3.655088e+06                   0   
3  18.499374  73.808299  7.716971e+06  3.655088e+06                   0   
4  18.498757  73.809519  7.717221e+06  3.655088e+06                   0   
5  18.498140  73.810738  7.717471e+06  3.655088e+06                   0   
6  18.497523  73.811957  7.717721e+06  3.655088e+06                   0   
7  18.496906  73.813177  7.717971e+06  3.655088e+06                   0   
8  18.496289  73.814396  7.718221e+06  3.655088e+06                   0   
9  18.495672  73.815615  7.718471e+06  3.655088e+06                   0   

   Distance to Indian restaurant  
0                     704.911967  
1                     333.979151  
2                     566.500372  
3                     635.330995  
4                     629.105553  
5                     585.984505  
6                     419.528227  
7                     341.904119  
8                     356.618949  
9                     440.728730

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Italian restaurants in radius of 400 meters**.

In [41]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ind_distance = np.array(df_roi_locations['Distance to Indian restaurant']>=200)
print('Locations with no Indian restaurants within 400m:', good_ind_distance.sum())

good_locations = np.logical_and(good_res_count, good_ind_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 333
Locations with no Indian restaurants within 400m: 307
Locations with both conditions met: 302


Let's see how this looks on a map.

In [42]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_pune = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_pune)
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune) 
folium.GeoJson(PuneAdminWards, style_function=wards_style, name='geojson').add_to(map_pune)
map_pune

Looking good. We now have a bunch of locations fairly close to Alexanderplatz (mostly in Kreuzberg, Friedrichshain and south-east corner of Mitte boroughs), and we know that each of those locations has no more than two restaurants in radius of 250m, and no Italian restaurant closer than 400m. Any of those locations is a potential candidate for a new Italian restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [43]:
map_pune = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)
folium.GeoJson(PuneAdminWards, style_function=wards_style, name='geojson').add_to(map_pune)
map_pune

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Italian restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [44]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_pune = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_pune)
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_pune) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)
folium.GeoJson(PuneAdminWards, style_function=wards_style, name='geojson').add_to(map_pune)
map_pune

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [45]:
map_pune = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(pune_center).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_pune) 
folium.GeoJson(PuneAdminWards, style_function=wards_style, name='geojson').add_to(map_pune)
map_pune

Let's zoom in on candidate areas in **Kothrud**:

In [46]:
map_pune = folium.Map(location=[18.507399,73.807648], zoom_start=15)
folium.Marker(pune_center).add_to(map_pune)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_pune) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)
folium.GeoJson(PuneAdminWards, style_function=wards_style, name='geojson').add_to(map_pune)
map_pune

...and candidate areas in **Karve Nagar**:

In [47]:
map_pune = folium.Map(location=[18.489759, 73.820297], zoom_start=15)
folium.Marker(pune_center).add_to(map_pune)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_pune) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)
folium.GeoJson(PuneAdminWards, style_function=wards_style, name='geojson').add_to(map_pune)
map_pune

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [48]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(google_api_key, lat, lon).replace(', India', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, pune_center_x, pune_center_y)
    print('{}{} => {:.1f}km from Deccan'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

Sno 120, Kishkindha Nagar, Nr Vitthal Mandir, Kothrud,, Kishkinda Nagar, Kothrud, Pune, Maharashtra 411038 => 4.4km from Deccan
1, Tejas Society, Dahanukar Colony, Kothrud, Pune, Maharashtra 411038 => 5.6km from Deccan
Shree Bunglow, Deccan Gymkhana, Pune, Maharashtra 411004 => 2.2km from Deccan
37/2, Erandawana Opp. Waman Niwas, Pandurang Colony, Erandwane, Pune, Maharashtra 411038 => 3.0km from Deccan
B-304, Balwantpuram Samrajya, Pethkar Projects,, Paud Road, Pune, Maharashtra, Shivtirthanagar, Matoba Nagar, Kothrud, Pune, Maharashtra 411038 => 5.4km from Deccan
C-25, Paschimanagri, Kothrud, Pune, Maharashtra 411038 => 5.0km from Deccan
Yogendra Society, Shastri Nagar Rd, Shree Colony, Azad Nagar, Kothrud, Pune, Maharashtra 411058 => 5.8km from Deccan
12, Shilpa Housing Society, Yashashree Society, Rambaug Colony, Kothrud, Pune, Maharashtra 411038 => 3.2km from Deccan
Survey Number 128/2, Plot No. 24, Lane No.1 , Navket

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Italian restaurants nearby, all zones being fairly close to city center (all less than 4km from Deccan, and about half of those less than 2km from Deccan). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located in Kothrud and Karve Nagar wards, which we have identified as interesting, fairly close to city center and well connected by public transport.

In [49]:
map_pune = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(pune_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_pune)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_pune) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_pune)
map_pune

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants in Pune (~2000 in our initial area of interest which was 10x10km around Deccan), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected north and west from Deccan, so we focused our attention to areas west, south-west and north-west, corresponding to wards Kothrud, Karve Nagar. Another ward was identified as potentially interesting (Pashan, north-west from Deccan), but our attention was focused on Kothrud and Karve Nagar which offer a combination of closeness to city center, strong socio-economic dynamics *and* a number of pockets of low restaurant density.

After directing our attention to this more narrow area of interest (covering approx. 5x5km south-west from Deccan) we first created a dense grid of location candidates (spaced 250m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Indian restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Indian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Pune center but not crowded with existing restaurants (particularly Indian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Pune areas close to center with low number of restaurants (particularly Indian restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Indian restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general wards that justify further analysis (Kothrud and Karve Nagar), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.